In [1]:
# author - Richard Liao 
# Dec 26 2016
import numpy as np
import pandas as pd

from collections import defaultdict
import re

from bs4 import BeautifulSoup

import sys
import os

os.environ['KERAS_BACKEND']='tensorflow'

from keras.preprocessing.text import Tokenizer, text_to_word_sequence
from keras.preprocessing.sequence import pad_sequences
from keras.utils.np_utils import to_categorical

from keras.layers import Embedding
from keras.layers import Dense, Input, Flatten
from keras.layers import Conv1D, MaxPooling1D, Embedding, Dropout, LSTM, GRU, Bidirectional, TimeDistributed
from keras.models import Model

from keras import backend as K
from keras.engine.topology import Layer, InputSpec
from keras import initializers

import tensorflow as tf
from keras.backend.tensorflow_backend import set_session




Using TensorFlow backend.


In [2]:
def gpu_alloc(device_id):
    os.environ["CUDA_VISIBLE_DEVICES"]=device_id
    config = tf.ConfigProto()
    config.gpu_options.allow_growth = True
    set_session(tf.Session(config=config))

In [3]:
gpu_alloc("1")

# Data


In [4]:
MAX_SENT_LENGTH = 40
MAX_SENTS = 10
MAX_NB_WORDS = 20000
EMBEDDING_DIM = 100
VALIDATION_SPLIT = 0.2
NUM_EPOCHS = 100
BATCH_SIZE = 50

def clean_str(string):
    """
    Tokenization/string cleaning for dataset
    Every dataset is lower cased except
    """
    string = re.sub(r"\\", "", string)    
    string = re.sub(r"\'", "", string)    
    string = re.sub(r"\"", "", string)    
    return string.strip().lower()

data_train = pd.read_csv('./dat/imdb/labeledTrainData.tsv', sep='\t')
print(data_train.shape)

from nltk import tokenize

reviews = []
labels = []
texts = []

for idx in range(data_train.review.shape[0]):
    print('Parsing review ' + str(idx))
    text = BeautifulSoup(data_train.review[idx]).get_text()
    text = clean_str(text)#.get_text().encode('ascii','ignore'))
    #print('Text:\n' + text)
    texts.append(text)
    sentences = tokenize.sent_tokenize(text)
    reviews.append(sentences)
    '''
    for sent in sentences:
          print('Sentence:\n' + sent)
    '''
    labels.append(data_train.sentiment[idx])

tokenizer = Tokenizer(nb_words=MAX_NB_WORDS)
tokenizer.fit_on_texts(texts)

data = np.zeros((len(texts), MAX_SENTS, MAX_SENT_LENGTH), dtype='int32')

for i, sentences in enumerate(reviews):
    for j, sent in enumerate(sentences):	
        if j< MAX_SENTS:
            wordTokens = text_to_word_sequence(sent)
            k=0
            for _, word in enumerate(wordTokens):
                if k<MAX_SENT_LENGTH and tokenizer.word_index[word]<MAX_NB_WORDS:
                    data[i,j,k] = tokenizer.word_index[word]
                    k=k+1                    
                    
word_index = tokenizer.word_index
print('Total %s unique tokens.' % len(word_index))

labels = to_categorical(np.asarray(labels))
print('Shape of data tensor:', data.shape)
print('Shape of label tensor:', labels.shape)

indices = np.arange(data.shape[0])
np.random.shuffle(indices)
data = data[indices]
labels = labels[indices]
nb_validation_samples = int(VALIDATION_SPLIT * data.shape[0])

x_train = data[:-nb_validation_samples]
y_train = labels[:-nb_validation_samples]
x_val = data[-nb_validation_samples:]
y_val = labels[-nb_validation_samples:]

print('Number of positive and negative reviews in traing and validation set')
print(y_train.sum(axis=0))
print(y_val.sum(axis=0))



(25000, 3)
Parsing review 0
Parsing review 1
Parsing review 2
Parsing review 3
Parsing review 4
Parsing review 5
Parsing review 6
Parsing review 7
Parsing review 8
Parsing review 9
Parsing review 10
Parsing review 11
Parsing review 12
Parsing review 13
Parsing review 14
Parsing review 15
Parsing review 16
Parsing review 17
Parsing review 18
Parsing review 19
Parsing review 20
Parsing review 21
Parsing review 22
Parsing review 23
Parsing review 24
Parsing review 25
Parsing review 26
Parsing review 27
Parsing review 28
Parsing review 29
Parsing review 30
Parsing review 31
Parsing review 32
Parsing review 33
Parsing review 34
Parsing review 35
Parsing review 36
Parsing review 37
Parsing review 38
Parsing review 39
Parsing review 40
Parsing review 41
Parsing review 42
Parsing review 43
Parsing review 44
Parsing review 45
Parsing review 46
Parsing review 47
Parsing review 48
Parsing review 49
Parsing review 50
Parsing review 51
Parsing review 52
Parsing review 53
Parsing review 54
Parsing r

/opt/anaconda3/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("lxml"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /opt/anaconda3/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "lxml")

  markup_type=markup_type))


Parsing review 202
Parsing review 203
Parsing review 204
Parsing review 205
Parsing review 206
Parsing review 207
Parsing review 208
Parsing review 209
Parsing review 210
Parsing review 211
Parsing review 212
Parsing review 213
Parsing review 214
Parsing review 215
Parsing review 216
Parsing review 217
Parsing review 218
Parsing review 219
Parsing review 220
Parsing review 221
Parsing review 222
Parsing review 223
Parsing review 224
Parsing review 225
Parsing review 226
Parsing review 227
Parsing review 228
Parsing review 229
Parsing review 230
Parsing review 231
Parsing review 232
Parsing review 233
Parsing review 234
Parsing review 235
Parsing review 236
Parsing review 237
Parsing review 238
Parsing review 239
Parsing review 240
Parsing review 241
Parsing review 242
Parsing review 243
Parsing review 244
Parsing review 245
Parsing review 246
Parsing review 247
Parsing review 248
Parsing review 249
Parsing review 250
Parsing review 251
Parsing review 252
Parsing review 253
Parsing revi

Parsing review 807
Parsing review 808
Parsing review 809
Parsing review 810
Parsing review 811
Parsing review 812
Parsing review 813
Parsing review 814
Parsing review 815
Parsing review 816
Parsing review 817
Parsing review 818
Parsing review 819
Parsing review 820
Parsing review 821
Parsing review 822
Parsing review 823
Parsing review 824
Parsing review 825
Parsing review 826
Parsing review 827
Parsing review 828
Parsing review 829
Parsing review 830
Parsing review 831
Parsing review 832
Parsing review 833
Parsing review 834
Parsing review 835
Parsing review 836
Parsing review 837
Parsing review 838
Parsing review 839
Parsing review 840
Parsing review 841
Parsing review 842
Parsing review 843
Parsing review 844
Parsing review 845
Parsing review 846
Parsing review 847
Parsing review 848
Parsing review 849
Parsing review 850
Parsing review 851
Parsing review 852
Parsing review 853
Parsing review 854
Parsing review 855
Parsing review 856
Parsing review 857
Parsing review 858
Parsing revi

Parsing review 1408
Parsing review 1409
Parsing review 1410
Parsing review 1411
Parsing review 1412
Parsing review 1413
Parsing review 1414
Parsing review 1415
Parsing review 1416
Parsing review 1417
Parsing review 1418
Parsing review 1419
Parsing review 1420
Parsing review 1421
Parsing review 1422
Parsing review 1423
Parsing review 1424
Parsing review 1425
Parsing review 1426
Parsing review 1427
Parsing review 1428
Parsing review 1429
Parsing review 1430
Parsing review 1431
Parsing review 1432
Parsing review 1433
Parsing review 1434
Parsing review 1435
Parsing review 1436
Parsing review 1437
Parsing review 1438
Parsing review 1439
Parsing review 1440
Parsing review 1441
Parsing review 1442
Parsing review 1443
Parsing review 1444
Parsing review 1445
Parsing review 1446
Parsing review 1447
Parsing review 1448
Parsing review 1449
Parsing review 1450
Parsing review 1451
Parsing review 1452
Parsing review 1453
Parsing review 1454
Parsing review 1455
Parsing review 1456
Parsing review 1457


...

Parsing review 23933
Parsing review 23934
Parsing review 23935
Parsing review 23936
Parsing review 23937
Parsing review 23938
Parsing review 23939
Parsing review 23940
Parsing review 23941
Parsing review 23942
Parsing review 23943
Parsing review 23944
Parsing review 23945
Parsing review 23946
Parsing review 23947
Parsing review 23948
Parsing review 23949
Parsing review 23950
Parsing review 23951
Parsing review 23952
Parsing review 23953
Parsing review 23954
Parsing review 23955
Parsing review 23956
Parsing review 23957
Parsing review 23958
Parsing review 23959
Parsing review 23960
Parsing review 23961
Parsing review 23962
Parsing review 23963
Parsing review 23964
Parsing review 23965
Parsing review 23966
Parsing review 23967
Parsing review 23968
Parsing review 23969
Parsing review 23970
Parsing review 23971
Parsing review 23972
Parsing review 23973
Parsing review 23974
Parsing review 23975
Parsing review 23976
Parsing review 23977
Parsing review 23978
Parsing review 23979
Parsing revie

Parsing review 24336
Parsing review 24337
Parsing review 24338
Parsing review 24339
Parsing review 24340
Parsing review 24341
Parsing review 24342
Parsing review 24343
Parsing review 24344
Parsing review 24345
Parsing review 24346
Parsing review 24347
Parsing review 24348
Parsing review 24349
Parsing review 24350
Parsing review 24351
Parsing review 24352
Parsing review 24353
Parsing review 24354
Parsing review 24355
Parsing review 24356
Parsing review 24357
Parsing review 24358
Parsing review 24359
Parsing review 24360
Parsing review 24361
Parsing review 24362
Parsing review 24363
Parsing review 24364
Parsing review 24365
Parsing review 24366
Parsing review 24367
Parsing review 24368
Parsing review 24369
Parsing review 24370
Parsing review 24371
Parsing review 24372
Parsing review 24373
Parsing review 24374
Parsing review 24375
Parsing review 24376
Parsing review 24377
Parsing review 24378
Parsing review 24379
Parsing review 24380
Parsing review 24381
Parsing review 24382
Parsing revie

Parsing review 24745
Parsing review 24746
Parsing review 24747
Parsing review 24748
Parsing review 24749
Parsing review 24750
Parsing review 24751
Parsing review 24752
Parsing review 24753
Parsing review 24754
Parsing review 24755
Parsing review 24756
Parsing review 24757
Parsing review 24758
Parsing review 24759
Parsing review 24760
Parsing review 24761
Parsing review 24762
Parsing review 24763
Parsing review 24764
Parsing review 24765
Parsing review 24766
Parsing review 24767
Parsing review 24768
Parsing review 24769
Parsing review 24770
Parsing review 24771
Parsing review 24772
Parsing review 24773
Parsing review 24774
Parsing review 24775
Parsing review 24776
Parsing review 24777
Parsing review 24778
Parsing review 24779
Parsing review 24780
Parsing review 24781
Parsing review 24782
Parsing review 24783
Parsing review 24784
Parsing review 24785
Parsing review 24786
Parsing review 24787
Parsing review 24788
Parsing review 24789
Parsing review 24790
Parsing review 24791
Parsing revie

/home/elsallab/.local/lib/python3.6/site-packages/keras_preprocessing/text.py:177: UserWarning: The `nb_words` argument in `Tokenizer` has been renamed `num_words`.
  warnings.warn('The `nb_words` argument in `Tokenizer` '


Total 81501 unique tokens.
Shape of data tensor: (25000, 10, 40)
Shape of label tensor: (25000, 2)
Number of positive and negative reviews in traing and validation set
[  9993.  10007.]
[ 2507.  2493.]


# Model


In [5]:
GLOVE_DIR = "./dat/glove"
embeddings_index = {}
f = open(os.path.join(GLOVE_DIR, 'glove.6B.100d.txt'))
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs

f.close()

print('Total %s word vectors.' % len(embeddings_index))

embedding_matrix = np.random.random((len(word_index) + 1, EMBEDDING_DIM))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector

embedding_layer = Embedding(len(word_index) + 1,
                            EMBEDDING_DIM,
                            weights=[embedding_matrix],
                            input_length=MAX_SENT_LENGTH,
                            trainable=True)

sentence_input = Input(shape=(MAX_SENT_LENGTH,), dtype='int32')
embedded_sequences = embedding_layer(sentence_input)
l_lstm = Bidirectional(LSTM(100))(embedded_sequences)
sentEncoder = Model(sentence_input, l_lstm)
print(sentEncoder.summary())
review_input = Input(shape=(MAX_SENTS,MAX_SENT_LENGTH), dtype='int32')
review_encoder = TimeDistributed(sentEncoder)(review_input)
print(review_encoder.shape)
l_lstm_sent = Bidirectional(LSTM(100))(review_encoder)
preds = Dense(2, activation='softmax')(l_lstm_sent)
model = Model(review_input, preds)

model.compile(loss='categorical_crossentropy',
              optimizer='rmsprop',
              metrics=['acc'])



Total 7396 word vectors.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 40)                0         
_________________________________________________________________
embedding_1 (Embedding)      (None, 40, 100)           8150200   
_________________________________________________________________
bidirectional_1 (Bidirection (None, 200)               160800    
Total params: 8,311,000
Trainable params: 8,311,000
Non-trainable params: 0
_________________________________________________________________
None
(?, 10, 200)


In [6]:
print(model.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 10, 40)            0         
_________________________________________________________________
time_distributed_1 (TimeDist (None, 10, 200)           8311000   
_________________________________________________________________
bidirectional_2 (Bidirection (None, 200)               240800    
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 402       
Total params: 8,552,202
Trainable params: 8,552,202
Non-trainable params: 0
_________________________________________________________________
None


In [7]:

print("model fitting - Hierachical LSTM")
print(model.summary())
model.fit(x_train, y_train, validation_data=(x_val, y_val),
          nb_epoch=NUM_EPOCHS, batch_size=BATCH_SIZE)


model fitting - Hierachical LSTM
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 10, 40)            0         
_________________________________________________________________
time_distributed_1 (TimeDist (None, 10, 200)           8311000   
_________________________________________________________________
bidirectional_2 (Bidirection (None, 200)               240800    
_________________________________________________________________
dense_1 (Dense)              (None, 2)                 402       
Total params: 8,552,202
Trainable params: 8,552,202
Non-trainable params: 0
_________________________________________________________________
None


/opt/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:5: UserWarning: The `nb_epoch` argument in `fit` has been renamed `epochs`.
  """


Train on 20000 samples, validate on 5000 samples
Epoch 1/100
20000/20000 [==============================] - 99s 5ms/step - loss: 0.5624 - acc: 0.7024 - val_loss: 0.3887 - val_acc: 0.8246
Epoch 2/100
20000/20000 [==============================] - 108s 5ms/step - loss: 0.3448 - acc: 0.8519 - val_loss: 0.3063 - val_acc: 0.8686
Epoch 3/100
20000/20000 [==============================] - 109s 5ms/step - loss: 0.2558 - acc: 0.8976 - val_loss: 0.2761 - val_acc: 0.8830
Epoch 4/100
20000/20000 [==============================] - 109s 5ms/step - loss: 0.2055 - acc: 0.9205 - val_loss: 0.2823 - val_acc: 0.8878
Epoch 5/100
20000/20000 [==============================] - 108s 5ms/step - loss: 0.1641 - acc: 0.9384 - val_loss: 0.3572 - val_acc: 0.8562
Epoch 6/100
20000/20000 [==============================] - 109s 5ms/step - loss: 0.1309 - acc: 0.9521 - val_loss: 0.3385 - val_acc: 0.8792
Epoch 7/100
20000/20000 [==============================] - 109s 5ms/step - loss: 0.0985 - acc: 0.9659 - val_loss: 0.33

KeyboardInterrupt: 

# Test

In [ ]:

data_test = pd.read_csv('./dat/imdb/labeledTrainData.tsv', sep='\t')
print(data_test.shape)


reviews = []
texts = []

for idx in range(data_test.review.shape[0]):
    print('Parsing review ' + str(idx))
    text = BeautifulSoup(data_test.review[idx]).get_text()
    text = clean_str(text)#.get_text().encode('ascii','ignore'))

    texts.append(text)
    sentences = tokenize.sent_tokenize(text)
    reviews.append(sentences)


data = np.zeros((len(texts), MAX_SENTS, MAX_SENT_LENGTH), dtype='int32')

for i, sentences in enumerate(reviews):
    for j, sent in enumerate(sentences):	
        if j< MAX_SENTS:
            wordTokens = text_to_word_sequence(sent)
            k=0
            for _, word in enumerate(wordTokens):
                if k<MAX_SENT_LENGTH and tokenizer.word_index[word]<MAX_NB_WORDS:
                    data[i,j,k] = tokenizer.word_index[word]
                    k=k+1                    
                    
test_input_data = data
test_texts = list(data_test.review.apply(BeautifulSoup).apply(BeautifulSoup.get_text).apply(clean_str))

(25000, 3)
Parsing review 0
Parsing review 1
Parsing review 2
Parsing review 3
Parsing review 4
Parsing review 5
Parsing review 6
Parsing review 7
Parsing review 8
Parsing review 9
Parsing review 10
Parsing review 11
Parsing review 12
Parsing review 13
Parsing review 14
Parsing review 15
Parsing review 16
Parsing review 17
Parsing review 18
Parsing review 19
Parsing review 20
Parsing review 21
Parsing review 22
Parsing review 23
Parsing review 24
Parsing review 25
Parsing review 26
Parsing review 27
Parsing review 28
Parsing review 29
Parsing review 30
Parsing review 31
Parsing review 32
Parsing review 33
Parsing review 34
Parsing review 35
Parsing review 36
Parsing review 37
Parsing review 38
Parsing review 39
Parsing review 40
Parsing review 41
Parsing review 42
Parsing review 43
Parsing review 44
Parsing review 45
Parsing review 46
Parsing review 47
Parsing review 48
Parsing review 49
Parsing review 50
Parsing review 51
Parsing review 52
Parsing review 53
Parsing review 54
Parsing r

/opt/anaconda3/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("lxml"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /opt/anaconda3/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "lxml")

  markup_type=markup_type))


Parsing review 209
Parsing review 210
Parsing review 211
Parsing review 212
Parsing review 213
Parsing review 214
Parsing review 215
Parsing review 216
Parsing review 217
Parsing review 218
Parsing review 219
Parsing review 220
Parsing review 221
Parsing review 222
Parsing review 223
Parsing review 224
Parsing review 225
Parsing review 226
Parsing review 227
Parsing review 228
Parsing review 229
Parsing review 230
Parsing review 231
Parsing review 232
Parsing review 233
Parsing review 234
Parsing review 235
Parsing review 236
Parsing review 237
Parsing review 238
Parsing review 239
Parsing review 240
Parsing review 241
Parsing review 242
Parsing review 243
Parsing review 244
Parsing review 245
Parsing review 246
Parsing review 247
Parsing review 248
Parsing review 249
Parsing review 250
Parsing review 251
Parsing review 252
Parsing review 253
Parsing review 254
Parsing review 255
Parsing review 256
Parsing review 257
Parsing review 258
Parsing review 259
Parsing review 260
Parsing revi

Parsing review 807
Parsing review 808
Parsing review 809
Parsing review 810
Parsing review 811
Parsing review 812
Parsing review 813
Parsing review 814
Parsing review 815
Parsing review 816
Parsing review 817
Parsing review 818
Parsing review 819
Parsing review 820
Parsing review 821
Parsing review 822
Parsing review 823
Parsing review 824
Parsing review 825
Parsing review 826
Parsing review 827
Parsing review 828
Parsing review 829
Parsing review 830
Parsing review 831
Parsing review 832
Parsing review 833
Parsing review 834
Parsing review 835
Parsing review 836
Parsing review 837
Parsing review 838
Parsing review 839
Parsing review 840
Parsing review 841
Parsing review 842
Parsing review 843
Parsing review 844
Parsing review 845
Parsing review 846
Parsing review 847
Parsing review 848
Parsing review 849
Parsing review 850
Parsing review 851
Parsing review 852
Parsing review 853
Parsing review 854
Parsing review 855
Parsing review 856
Parsing review 857
Parsing review 858
Parsing revi

Parsing review 1410
Parsing review 1411
Parsing review 1412
Parsing review 1413
Parsing review 1414
Parsing review 1415
Parsing review 1416
Parsing review 1417
Parsing review 1418
Parsing review 1419
Parsing review 1420
Parsing review 1421
Parsing review 1422
Parsing review 1423
Parsing review 1424
Parsing review 1425
Parsing review 1426
Parsing review 1427
Parsing review 1428
Parsing review 1429
Parsing review 1430
Parsing review 1431
Parsing review 1432
Parsing review 1433
Parsing review 1434
Parsing review 1435
Parsing review 1436
Parsing review 1437
Parsing review 1438
Parsing review 1439
Parsing review 1440
Parsing review 1441
Parsing review 1442
Parsing review 1443
Parsing review 1444
Parsing review 1445
Parsing review 1446
Parsing review 1447
Parsing review 1448
Parsing review 1449
Parsing review 1450
Parsing review 1451
Parsing review 1452
Parsing review 1453
Parsing review 1454
Parsing review 1455
Parsing review 1456
Parsing review 1457
Parsing review 1458
Parsing review 1459


...

Parsing review 23239
Parsing review 23240
Parsing review 23241
Parsing review 23242
Parsing review 23243
Parsing review 23244
Parsing review 23245
Parsing review 23246
Parsing review 23247
Parsing review 23248
Parsing review 23249
Parsing review 23250
Parsing review 23251
Parsing review 23252
Parsing review 23253
Parsing review 23254
Parsing review 23255
Parsing review 23256
Parsing review 23257
Parsing review 23258
Parsing review 23259
Parsing review 23260
Parsing review 23261
Parsing review 23262
Parsing review 23263
Parsing review 23264
Parsing review 23265
Parsing review 23266
Parsing review 23267
Parsing review 23268
Parsing review 23269
Parsing review 23270
Parsing review 23271
Parsing review 23272
Parsing review 23273
Parsing review 23274
Parsing review 23275
Parsing review 23276
Parsing review 23277
Parsing review 23278
Parsing review 23279
Parsing review 23280
Parsing review 23281
Parsing review 23282
Parsing review 23283
Parsing review 23284
Parsing review 23285
Parsing revie

Parsing review 23643
Parsing review 23644
Parsing review 23645
Parsing review 23646
Parsing review 23647
Parsing review 23648
Parsing review 23649
Parsing review 23650
Parsing review 23651
Parsing review 23652
Parsing review 23653
Parsing review 23654
Parsing review 23655
Parsing review 23656
Parsing review 23657
Parsing review 23658
Parsing review 23659
Parsing review 23660
Parsing review 23661
Parsing review 23662
Parsing review 23663
Parsing review 23664
Parsing review 23665
Parsing review 23666
Parsing review 23667
Parsing review 23668
Parsing review 23669
Parsing review 23670
Parsing review 23671
Parsing review 23672
Parsing review 23673
Parsing review 23674
Parsing review 23675
Parsing review 23676
Parsing review 23677
Parsing review 23678
Parsing review 23679
Parsing review 23680
Parsing review 23681
Parsing review 23682
Parsing review 23683
Parsing review 23684
Parsing review 23685
Parsing review 23686
Parsing review 23687
Parsing review 23688
Parsing review 23689
Parsing revie

Parsing review 24048
Parsing review 24049
Parsing review 24050
Parsing review 24051
Parsing review 24052
Parsing review 24053
Parsing review 24054
Parsing review 24055
Parsing review 24056
Parsing review 24057
Parsing review 24058
Parsing review 24059
Parsing review 24060
Parsing review 24061
Parsing review 24062
Parsing review 24063
Parsing review 24064
Parsing review 24065
Parsing review 24066
Parsing review 24067
Parsing review 24068
Parsing review 24069
Parsing review 24070
Parsing review 24071
Parsing review 24072
Parsing review 24073
Parsing review 24074
Parsing review 24075
Parsing review 24076
Parsing review 24077
Parsing review 24078
Parsing review 24079
Parsing review 24080
Parsing review 24081
Parsing review 24082
Parsing review 24083
Parsing review 24084
Parsing review 24085
Parsing review 24086
Parsing review 24087
Parsing review 24088
Parsing review 24089
Parsing review 24090
Parsing review 24091
Parsing review 24092
Parsing review 24093
Parsing review 24094
Parsing revie

Parsing review 24465
Parsing review 24466
Parsing review 24467
Parsing review 24468
Parsing review 24469
Parsing review 24470
Parsing review 24471
Parsing review 24472
Parsing review 24473
Parsing review 24474
Parsing review 24475
Parsing review 24476
Parsing review 24477
Parsing review 24478
Parsing review 24479
Parsing review 24480
Parsing review 24481
Parsing review 24482
Parsing review 24483
Parsing review 24484
Parsing review 24485
Parsing review 24486
Parsing review 24487
Parsing review 24488
Parsing review 24489
Parsing review 24490
Parsing review 24491
Parsing review 24492
Parsing review 24493
Parsing review 24494
Parsing review 24495
Parsing review 24496
Parsing review 24497
Parsing review 24498
Parsing review 24499
Parsing review 24500
Parsing review 24501
Parsing review 24502
Parsing review 24503
Parsing review 24504
Parsing review 24505
Parsing review 24506
Parsing review 24507
Parsing review 24508
Parsing review 24509
Parsing review 24510
Parsing review 24511
Parsing revie

Parsing review 24887
Parsing review 24888
Parsing review 24889
Parsing review 24890
Parsing review 24891
Parsing review 24892
Parsing review 24893
Parsing review 24894
Parsing review 24895
Parsing review 24896
Parsing review 24897
Parsing review 24898
Parsing review 24899
Parsing review 24900
Parsing review 24901
Parsing review 24902
Parsing review 24903
Parsing review 24904
Parsing review 24905
Parsing review 24906
Parsing review 24907
Parsing review 24908
Parsing review 24909
Parsing review 24910
Parsing review 24911
Parsing review 24912
Parsing review 24913
Parsing review 24914
Parsing review 24915
Parsing review 24916
Parsing review 24917
Parsing review 24918
Parsing review 24919
Parsing review 24920
Parsing review 24921
Parsing review 24922
Parsing review 24923
Parsing review 24924
Parsing review 24925
Parsing review 24926
Parsing review 24927
Parsing review 24928
Parsing review 24929
Parsing review 24930
Parsing review 24931
Parsing review 24932
Parsing review 24933
Parsing revie

In [ ]:
for i, rev in enumerate(data_test.review):
    print(rev)
    test_input = test_input_data[i].copy()
    test_input = np.reshape(test_input, (1,test_input.shape[0], test_input.shape[1]))
    prediction = model.predict(test_input)
    print('Prediction: ', prediction)
    sentiment = np.argmax(prediction)
    print('Sentiment: ' + str(sentiment))

With all this stuff going down at the moment with MJ i've started listening to his music, watching the odd documentary here and there, watched The Wiz and watched Moonwalker again. Maybe i just want to get a certain insight into this guy who i thought was really cool in the eighties just to maybe make up my mind whether he is guilty or innocent. Moonwalker is part biography, part feature film which i remember going to see at the cinema when it was originally released. Some of it has subtle messages about MJ's feeling towards the press and also the obvious message of drugs are bad m'kay.<br /><br />Visually impressive but of course this is all about Michael Jackson so unless you remotely like MJ in anyway then you are going to hate this and find it boring. Some may call MJ an egotist for consenting to the making of this movie BUT MJ and most of his fans would say that he made it for the fans which if true is really nice of him.<br /><br />The actual feature film bit when it finally star

Prediction:  [[  1.77490248e-04   9.99822557e-01]]
Sentiment: 1
This movie could have been very good, but comes up way short. Cheesy special effects and so-so acting. I could have looked past that if the story wasn't so lousy. If there was more of a background story, it would have been better. The plot centers around an evil Druid witch who is linked to this woman who gets migraines. The movie drags on and on and never clearly explains anything, it just keeps plodding on. Christopher Walken has a part, but it is completely senseless, as is most of the movie. This movie had potential, but it looks like some really bad made for TV movie. I would avoid this movie.
Prediction:  [[  1.00000000e+00   8.46977866e-09]]
Sentiment: 0
I watched this video at a friend's house. I'm glad I did not waste money buying this one. The video cover has a scene from the 1975 movie Capricorn One. The movie starts out with several clips of rocket blow-ups, most not related to manned flight. Sibrel's smoking g

Prediction:  [[ 0.85435015  0.14564987]]
Sentiment: 0
Most people, especially young people, may not understand this film. It looks like a story of loss, when it is actually a story about being alone. Some people may never feel loneliness at this level.<br /><br />Cheadles character Johnson reflected the total opposite of Sandlers character Fineman. Where Johnson felt trapped by his blessings, Fineman was trying to forget his life in the same perspective. Jada is a wonderful additive to the cast and Sandler pulls tears. Cheadle had the comic role and was a great supporter for Sandler.<br /><br />I see Oscars somewhere here. A very fine film. If you have ever lost and felt alone, this film will assure you that you're not alone.<br /><br />Jerry
Prediction:  [[  3.66093218e-08   1.00000000e+00]]
Sentiment: 1
\Soylent Green\" is one of the best and most disturbing science fiction movies of the 70's and still very persuasive even by today's standards. Although flawed and a little dated, the

Prediction:  [[  1.00000000e+00   1.27753195e-08]]
Sentiment: 0
Would anyone really watch this RUBBISH if it didn't contain little children running around nude? From a cinematic point of view it is probably one of the worst films I have encountered absolutely dire. Some perv woke up one day and thought I will make a film with little girls in and call it art, stick them in countryside and there isn't any need for a story or explanation of how they got there or why they don't appear to live anywhere or have parents because p*rn films don't need anything like that. I would comment on the rest of the film but I haven't ticked spoilers so I will just say avoid, avoid avoid and find yourself a proper film to watch
Prediction:  [[  1.00000000e+00   3.13690696e-09]]
Sentiment: 0
Unremarkable and unmemorable remake of an old, celebrated English film. Although it may be overly maligned as a total disaster (which it is not), it never builds any tension and betrays its TV origins. Richard Burton s

Prediction:  [[  1.00000000e+00   3.77530202e-10]]
Sentiment: 0
I found this movie quite by accident, but am happy that I did. Kenneth Branagh's performance came close to stealing this movie from Helena Bonham Carter, but their strong chemistry together made for a much more enjoyable movie. This movie brought to mind the excellent movies that Branagh made with Emma Thompson. Carter's star turn here as a disabled young women seeking to complete herself was as good a performance as I have seen from a female lead in a long time. Portraying a disabled person is hard to pull off, but with basically only her eyes to show her pain about her situation in life, she made it so believable. If this movie had come out after the current wave of movies with beautiful women \uglying\" themselves up for roles (Charlize Theron, Halle Berry), I fell sure Carter would have had strong consideration for an Oscar. If you run across this movie on cable late at night as I did, trust me, it is worth the lost sl

...

Prediction:  [[  1.93149205e-07   9.99999762e-01]]
Sentiment: 1
Hey now, yours truly, TheatreX, found this while grubbing through videos at the flea market, in almost new condition, and in reading the back of the box saw that it was somewhat of a \cult hit\" so of course it came home with me. <br /><br />What a strange film. The aunt and cousin of former first lady Jacqueline Bouvier Kennedy Onassis live in this decaying 28 room house out on Long Island (Suffolk Co.) and share the house with raccoons, cats, fleas (eyow!) and who knows what else. Suffolk Co. was all over them at one point for living in filth and old Jackie herself came by to set things right. Anyway, this is one strange pair, Big Edie and Little Edie...Edie (the daughter) always wears something over her head and dances, sings, and gives little asides to the camera that rarely make much sense. Big Edie (the mother, age 79) apparently likes to run around naked, and while we do get hints of what that might look like thankf

Prediction:  [[  1.00000000e+00   7.26323224e-10]]
Sentiment: 0
This will be brief. Let me first state that I'm agnostic and not exactly crazy about xtians, especially xtian fanatics. However, this documentary had a tone of the like of some teenager angry at his xtian mother for not letting him play video games. I just couldn't take it seriously. Mentioning how CharlesManson thought he was Christ to illustrate the point that xtianity can breed evil? i don't know it was just cheap and childish -- made the opposition look ignorant. Furthermore, the narrator just seemed snobby and pretentious. The delivery was complete overkill. I can't take this documentary seriously. Might appeal to an angry teenager piss3d off at his xtian mother for not letting him play video games.
Prediction:  [[  1.00000000e+00   9.58412127e-10]]
Sentiment: 0
When my own child is begging me to leave the opening show of this film, I know it is bad. I wanted to claw my eyes out. I wanted to reach through the screen a

Prediction:  [[  2.15509459e-07   9.99999762e-01]]
Sentiment: 1
You have to understand, when Wargames was released in 1983, it created a generation of wannabe computer hackers. The idea that a teenager could do anything of far reaching proportions, let alone deter a world war was novel and thrilling. Real computers were beginning to show up in people's homes, and for the first time, society was becoming interconnected in a way that made the movie's premise excitingly prescient. Granted, a talking computer that balanced it's free time between chess and global thermonuclear war was a bit far fetched, but the brilliant commentary on nuclear proliferation and the cold war made up for it. I've probably even heard of the hackers that this movie was actually based on.<br /><br />Fast forward 25 years, and we have a horrible mutant of a thing that I loathe to call a \sequel\", called Wargames: The Dead Code. I'll just dig right in. First of all, the plot hinges on a government operated gamblin

Prediction:  [[  2.84292082e-06   9.99997139e-01]]
Sentiment: 1
I'll be honest, this is one of the worst movies ever. If not, then it's VERY close. Ever seen a bad teen soap opera. Well this is like one of those. Except worse. For example: (POSSIBLY SPOILER) girl: I wanna go somewhere else.<br /><br />guy: all we need is here.<br /><br />girl: but I wanna take myself somewhere different.<br /><br />guy: I'll take YOU somewhere else.<br /><br />... Proceeding this line they have sex. The music is bad pop and bad punk rock. If you've EVER read the book, avoid this movie like the plague. They completely change the personalities of the characters and the events. Additionally, they just get rid of things. Also, the movie ends about before the book finishes. It is an AWFUL movie. So, if you haven't read the book, don't watch it. If you HAVE read the book, burn it (the movie). If you like stupid teen soap operas that are lower quality than your average low quality teen soap opera, go for it. 

Prediction:  [[  8.69050165e-09   1.00000000e+00]]
Sentiment: 1
The original is a relaxing watch, with some truly memorable animated sequences. Unfortunately, the sequel, while not the worst of the DTV sequels completely lacks the sparkle.<br /><br />The biggest letdown is a lack of a story. Like Belle's Magical World, the characters are told through a series of vignettes. Magical World, while marginally better, still manages to make a mess of the story. In between the vignettes, we see the mice at work, and I personally think the antics of Jaq and Gus are the redeeming merits of this movie.<br /><br />The first vignette is the best, about Cinderella getting used to being to being a princess. This is the best, because the mice were at their funniest here. The worst of the vignettes, when Jaq turns into a human, is cute at times, but has a lack of imagination. The last vignette, when Anastasia falls in love, was also cute. The problem was, I couldn't imagine Anastasia being friendly wit